#### Names of people in the group

Please write the names of the people in your group in the next cell.

Eivind Kjosbakken

In [0]:
# Deleting tables left from previous runs in case they still exist after deleting an inactive cluster
dbutils.fs.rm("/user", recurse=True)

Out[22]: True

In [0]:
# We need to install 'ipython_unittest' to run unittests in a Jupyter notebook
!pip install -q ipython_unittest

You should consider upgrading via the '/databricks/python3/bin/python -m pip install --upgrade pip' command.


In [0]:
# Loading PySpark modules that we need
import unittest
from collections import Counter
from pyspark.sql import DataFrame 
from pyspark.sql.types import *



#### Subtask 1: defining the schema for the data
Typically, the first thing to do before loading the data into a Spark cluster is to define the schema for the data. Look at the schema for 'badges' and try to define the schema for other tables similarly.

In [0]:
# Defining a schema for 'badges' table
badges_schema = StructType([StructField('UserId', IntegerType(), False),
                            StructField('Name', StringType(), False),
                            StructField('Date', TimestampType(), False),
                            StructField('Class', IntegerType(), False)])

# Defining a schema for 'posts' table
#since none of the fields in badges was nullable, I assume the same thing applies for the rest of the tables
#I am using IntegerType for any numbers, TimestampType for any dates or times, and StringType for the rest
posts_schema = StructType([StructField('Id', IntegerType(), False),
                            StructField('ParentID', IntegerType(), False),
                            StructField('PostTypeId', IntegerType(), False),
                            StructField('CreationDate', TimestampType(), False),
                            StructField('Score', IntegerType(), False),
                            StructField('ViewCount', IntegerType(), False),
                            StructField('Body', StringType(), False),
                            StructField('OwnerUserId', IntegerType(), False),
                            StructField('LastActivityDate', TimestampType(), False),
                            StructField('Title', StringType(), False),
                            StructField('Tags', StringType(), False), #should be arraytype but I don't think that works, instead I assume I can store it as a string,                                                                                                         #which I can then split into an array if needed
                            StructField('AnswerCount', IntegerType(), False),
                            StructField('CommentCount', IntegerType(), False),
                            StructField('FavoriteCount', IntegerType(), False),
                            StructField('CloseDate', TimestampType(), False)])
## YOUR IMPLEMENTATION ##

# Defining a schema for 'users' table
users_schema = StructType([StructField('Id', IntegerType(), False),
                            StructField('Reputation', IntegerType(), False), #reputation is an integer
                            StructField('CreationDate', TimestampType(), False),
                            StructField('DisplayName', StringType(), False),
                            StructField('LastAccessDate', TimestampType(), False),
                            StructField('AboutMe', StringType(), False),
                            StructField('Views', IntegerType(), False),
                            StructField('UpVotes', IntegerType(), False),
                            StructField('DownVotes', IntegerType(), False)])
## YOUR IMPLEMENTATION ##

# Defining a schema for 'comments' table
comments_schema = StructType([StructField('PostId', IntegerType(), False),
                            StructField('Score', IntegerType(), False),
                            StructField('Text', StringType(), False),
                            StructField('CreationDate', TimestampType(), False),
                            StructField('UserId', IntegerType(), False)])
## YOUR IMPLEMENTATION ##

#### Subtask 2: implementing two helper functions
Next, we need to implement two helper functions:
1. 'load_csv' that as input argument receives path for a CSV file and a schema and loads the CSV pointed by the path into a Spark DataFrame and returns the DataFrame;
2. 'save_df' receives a Spark DataFrame and saves it as a Parquet file on DBFS.

Note that the column separator in CSV files is TAB character ('\t') and the first row includes the name of the columns. 

BTW, DBFS is the name of the distributed filesystem used by Databricks Community Edition to store and access data.

In [0]:
def load_csv(source_file: "path for the CSV file to load", schema: "schema for the CSV file being loaded as a DataFrame") -> DataFrame:
      ## YOUR IMPLEMENTATION ##
    #using the read csv, seperating by the tab characther, and header=True makes the first row the name of the columns. 
    df = spark.read.csv(source_file, sep="\t", header=True, schema=schema)
    display(df)
    return df
def save_df(df: "DataFrame to be saved", table_name: "name under which the DataFrame will be saved") -> None:
    ## YOUR IMPLEMENTATION ##
    #using the .write.format() to save the df as parquet file, using mode(overwrite) so if I run it twice, it still works (only saves the last writing), and then saving it to the table_name
    df.write.format("parquet").mode('overwrite').saveAsTable(table_name)    
    
    

In [0]:
# Loading 'ipython_unittest' so we can use '%%unittest_main' magic command
%load_ext ipython_unittest

The ipython_unittest extension is already loaded. To reload it, use:
  %reload_ext ipython_unittest


#### Subtask 3: validating the implementation by running the tests

Run the cell below and make sure that all the tests run successfully. Moreover, at the end there should be four Parquet files named 'badges', 'comments', 'posts', and 'users' in '/user/hive/warehouse'.

Note that we assumed that the data for the project has already been stored on DBFS on the '/FileStore/tables/' path. (I mean as 'badges_csv.gz', 'comments_csv.gz', 'posts_csv.gz', and 'users_csv.gz'.)

In [0]:
%%unittest_main
class TestTask1(unittest.TestCase):
   
    # test 1
    def test_load_badges(self):
        result = load_csv(source_file="/FileStore/tables/badges__1__csv-2.gz", schema=badges_schema) # changed the location of the file to where i stored them
        self.assertIsNotNone(result, "Badges dataframe did not load successfully")
        self.assertIsInstance(result, DataFrame, "Result type is not of spark.sql.DataFrame")
        self.assertEqual(result.count(), 105640, "Number of records is not correct") 
        coulmn_names = Counter(map(str.lower, ['UserId', 'Name', 'Date', 'Class']))
        self.assertCountEqual(coulmn_names, Counter(map(str.lower, result.columns)),
                              "Missing column(s) or column name mismatch")
        
    # test 2
    def test_load_posts(self):
        result = load_csv(source_file="/FileStore/tables/posts__1__csv-2.gz", schema=posts_schema) # changed the location of the file
        self.assertIsNotNone(result, "Posts dataframe did not load successfully")
        self.assertIsInstance(result, DataFrame, "Result type is not of spark.sql.DataFrame")
        self.assertEqual(result.count(), 61432, "Number of records is not correct")

        coulmn_names = Counter(map(str.lower,
                                   ['Id', 'ParentId', 'PostTypeId', 'CreationDate', 'Score', 'ViewCount', 'Body', 'OwnerUserId',
                                    'LastActivityDate', 'Title', 'Tags', 'AnswerCount', 'CommentCount', 'FavoriteCount',
                                    'CloseDate']))
        self.assertCountEqual(coulmn_names, Counter(map(str.lower, result.columns)),
                              "Missing column(s) or column name mismatch")
    
    # test 3
    def test_load_comments(self):
        result = load_csv(source_file="/FileStore/tables/comments__1__csv-2.gz", schema=comments_schema) # changed the location of the file
        self.assertIsNotNone(result, "Comments dataframe did not load successfully")
        self.assertIsInstance(result, DataFrame, "Result type is not of spark.sql.DataFrame")
        self.assertEqual(result.count(), 58735, "Number of records is not correct")

        coulmn_names = Counter(map(str.lower, ['PostId', 'Score', 'Text', 'CreationDate', 'UserId']))
        self.assertCountEqual(coulmn_names, Counter(map(str.lower, result.columns)),
                              "Missing column(s) or column name mismatch")
    
    # test 4
    def test_load_users(self):
        result = load_csv(source_file="/FileStore/tables/users__1__csv-3.gz", schema=users_schema) # changed the location of the file
        self.assertIsNotNone(result, "Users dataframe did not load successfully")
        self.assertIsInstance(result, DataFrame, "Result type is not of spark.sql.DataFrame")
        self.assertEqual(result.count(), 91616, "Number of records is not correct")

        coulmn_names = Counter(map(str.lower,
                                   ['Id', 'Reputation', 'CreationDate', 'DisplayName', 'LastAccessDate', 'AboutMe',
                                    'Views', 'UpVotes', 'DownVotes']))
        self.assertCountEqual(coulmn_names, Counter(map(str.lower, result.columns)),
                              "Missing column(s) or column name mismatch")
    # test 5
    def test_save_dfs(self):
        dfs = [("/FileStore/tables/users__1__csv-3.gz", users_schema, "users"), # changed the location of the files
               ("/FileStore/tables/badges__1__csv-2.gz", badges_schema, "badges"),
               ("/FileStore/tables/comments__1__csv-2.gz", comments_schema, "comments"),
               ("/FileStore/tables/posts__1__csv-2.gz", posts_schema, "posts")
               ]

        for i in dfs:
            df = load_csv(source_file=i[0], schema=i[1])
            save_df(df, i[2])

Success.....
----------------------------------------------------------------------
Ran 5 tests in 36.643s

OK
Out[28]: <unittest.runner.TextTestResult run=5 errors=0 failures=0>

UserId Name Date Class 1 Informed 2014-05-13T23:06:44.000+0000 3 2 Autobiographer 2014-05-13T23:11:04.000+0000 3 4 Autobiographer 2014-05-13T23:20:53.000+0000 3 5 Autobiographer 2014-05-13T23:20:53.000+0000 3 8 Autobiographer 2014-05-13T23:20:53.000+0000 3 9 Autobiographer 2014-05-13T23:20:53.000+0000 3 11 Autobiographer 2014-05-13T23:25:53.000+0000 3 12 Autobiographer 2014-05-13T23:25:53.000+0000 3 17 Autobiographer 2014-05-13T23:25:53.000+0000 3 3 Informed 2014-05-13T23:27:23.000+0000 3 14 Informed 2014-05-13T23:27:35.000+0000 3 22 Autobiographer 2014-05-13T23:40:53.000+0000 3 24 Autobiographer 2014-05-13T23:40:53.000+0000 3 24 Informed 2014-05-13T23:41:05.000+0000 3 28 Autobiographer 2014-05-13T23:50:54.000+0000 3 29 Autobiographer 2014-05-13T23:50:54.000+0000 3 30 Autobiographer 2014-05-13T23:50:54.000+0000 3 6 Student 2014-05-13T23:50:54.000+0000 3 29 Supporter 2014-05-13T23:50:54.000+0000 3 32 Autobiographer 2014-05-13T23:55:57.000+0000 3 34 Autobiographer 2014-05-13T23:55:57.000+0000 3 35 Autobiographer 2014-05-13T23:55:57.000+0000 3 38 Autobiographer 2014-05-13T23:55:57.000+0000 3 37 Supporter 2014-05-13T23:55:57.000+0000 3 26 Editor 2014-05-14T00:00:58.000+0000 3 26 Supporter 2014-05-14T00:00:58.000+0000 3 38 Supporter 2014-05-14T00:00:58.000+0000 3 26 Teacher 2014-05-14T00:00:58.000+0000 3 36 Teacher 2014-05-14T00:00:58.000+0000 3 7 Citizen Patrol 2014-05-14T00:05:26.000+0000 3 5 Student 2014-05-14T00:05:58.000+0000 3 19 Supporter 2014-05-14T00:05:58.000+0000 3 41 Autobiographer 2014-05-14T00:12:25.000+0000 3 37 Precognitive 2014-05-14T00:12:25.000+0000 3 14 Precognitive 2014-05-14T00:12:25.000+0000 3 17 Precognitive 2014-05-14T00:12:25.000+0000 3 10 Precognitive 2014-05-14T00:12:25.000+0000 3 15 Precognitive 2014-05-14T00:12:25.000+0000 3 11 Precognitive 2014-05-14T00:12:25.000+0000 3 25 Precognitive 2014-05-14T00:12:25.000+0000 3 31 Precognitive 2014-05-14T00:12:25.000+0000 3 20 Precognitive 2014-05-14T00:12:25.000+0000 3 36 Student 2014-05-14T00:12:25.000+0000 3 3 Supporter 2014-05-14T00:12:25.000+0000 3 36 Supporter 2014-05-14T00:17:25.000+0000 3 34 Teacher 2014-05-14T00:17:25.000+0000 3 20 Supporter 2014-05-14T00:22:26.000+0000 3 46 Autobiographer 2014-05-14T00:27:25.000+0000 3 53 Autobiographer 2014-05-14T00:37:25.000+0000 3 51 Supporter 2014-05-14T00:37:25.000+0000 3 51 Citizen Patrol 2014-05-14T00:39:24.000+0000 3 55 Autobiographer 2014-05-14T00:49:48.000+0000 3 46 Student 2014-05-14T00:54:48.000+0000 3 22 Supporter 2014-05-14T00:54:48.000+0000 3 22 Teacher 2014-05-14T00:54:48.000+0000 3 51 Teacher 2014-05-14T00:54:48.000+0000 3 61 Autobiographer 2014-05-14T00:59:49.000+0000 3 62 Autobiographer 2014-05-14T00:59:49.000+0000 3 22 Citizen Patrol 2014-05-14T00:58:13.000+0000 3 9 Quorum 2014-05-14T01:12:25.000+0000 3 55 Precognitive 2014-05-14T01:12:25.000+0000 3 43 Precognitive 2014-05-14T01:12:25.000+0000 3 52 Precognitive 2014-05-14T01:12:25.000+0000 3 62 Precognitive 2014-05-14T01:12:25.000+0000 3 48 Precognitive 2014-05-14T01:12:25.000+0000 3 63 Precognitive 2014-05-14T01:12:25.000+0000 3 64 Precognitive 2014-05-14T01:12:25.000+0000 3 9 Talkative 2014-05-14T01:12:25.000+0000 3 66 Informed 2014-05-14T01:19:21.000+0000 3 66 Autobiographer 2014-05-14T01:19:49.000+0000 3 38 Citizen Patrol 2014-05-14T01:19:03.000+0000 3 64 Supporter 2014-05-14T01:19:49.000+0000 3 66 Supporter 2014-05-14T01:19:49.000+0000 3 66 Student 2014-05-14T01:34:49.000+0000 3 64 Informed 2014-05-14T01:35:57.000+0000 3 70 Informed 2014-05-14T01:50:35.000+0000 3 5 Informed 2014-05-14T01:55:55.000+0000 3 72 Autobiographer 2014-05-14T01:56:33.000+0000 3 73 Autobiographer 2014-05-14T01:56:33.000+0000 3 3 Critic 2014-05-14T01:56:33.000+0000 3 5 Critic 2014-05-14T01:56:33.000+0000 3 7 Critic 2014-05-14T01:56:33.000+0000 3 20 Critic 2014-05-14T01:56:33.000+0000 3 22 Critic 2014-05-14T01:56:33.000+0000 3 36 Critic 2014-05-14T01:56:33.000+0000 3 38 Critic 2014-05-14T01:56:33.000+0000 3 48 Critic 2014-05-14T01:56:33.000+0000 3 50 Critic 2014-05-14T01:56

PostId Score Text CreationDate UserId 5 9 dGhpcyBpcyBhIHN1cGVyIHRoZW9yZXRpY2FsIEFJIHF1ZXN0aW9uLiBBbiBpbnRlcmVzdGluZyBkaXNjdXNzaW9uISBidXQgb3V0IG9mIHBsYWNlLi4u 2014-05-14T00:23:15.000+0000 34 7 4 TGlzdCBxdWVzdGlvbnMgYXJlIHVzdWFsbHkgbm90IHN1aXRlZCBmb3IgU3RhY2sgRXhjaGFuZ2Ugd2Vic2l0ZXMgc2luY2UgdGhlcmUgaXNuJ3QgYW4gIm9iamVjdGl2ZSIgYW5zd2VyIG9yIGEgd2F5IHRvIG1lYXN1cmUgdGhlIHVzZWZ1bG5lc3Mgb2YgYW4gYW5zd2VyLiBIYXZpbmcgc2FpZCB0aGF0LCBvbmUgb2YgbXkgcmVjb21tZW5kYXRpb25zIHdvdWxkIGJlIE1hY0theSdzICJJbmZvcm1hdGlvbiBUaGVvcnksIEluZmVyZW5jZSwgYW5kIExlYXJuaW5nIEFsZ29yaXRobXMuIg== 2014-05-14T00:38:19.000+0000 51 7 3 VGhpcyBxdWVzdGlvbiBhcHBlYXJzIHRvIGJlIG9mZi10b3BpYyBiZWNhdXNlIGl0IGlzIGFza3MgZm9yIGEgZmF2b3JpdGUgcmVzb3VyY2UuICBPbiBvdGhlciBTRSBzaXRlcywgdGhpcyB3b3VsZCBpbW1lZGlhdGVseSBiZSBjbG9zZWQuICBTaW5jZSB0aGlzIGlzIGEgbmV3IHNpdGUsIHdlIHN0aWxsIGhhdmUgdG8gZGVjaWRlIGlmIHRoaXMgaXMgYSB2YWxpZCBxdWVzdGlvbiBoZXJl 2014-05-14T01:16:12.000+0000 66 15 3 VGhpcyBxdWVzdGlvbiBpcyBmYXIgdG9vIGJyb2FkLiBJdCBtYXkgYmUgc2FsdmFnZWQgYnkgcmVzdHJpY3RpbmcgdGhlIHF1ZXN0aW9uIHRvIGEgcGFydGljdWxhciB1c2UgY2FzZS4= 2014-05-14T02:00:22.000+0000 51 10 2 TmljZSBvbmUsIEBOaWNob2xhcy4uLiBBbm90aGVyIGJvb2sgZnJvbSBIYXN0aWUgYW5kIFRpYnNoaXJhbmkgaXMgW0ludHJvZHVjdGlvbiB0byBTdGF0aXN0aWNhbCBMZWFybmluZ10oaHR0cDovL3d3dy1iY2YudXNjLmVkdS9+Z2FyZXRoL0lTTC8pLCB3aGljaCBpcyBhIGJpdCBnZW50bGVyIG9mIGFuIGVudHJ5IGNvbXBhcmVkIHRvIEVTTC4= 2014-05-14T02:16:20.000+0000 24 7 0 RmFpciBlbm91Z2ggcmVnYXJkaW5nIHdoYXQgY29uc3RpdHV0ZXMgYSAidmFsaWQiIHF1ZXN0aW9uLCBhbHRob3VnaCBvbiBvdGhlciBTRSBzaXRlcyB0aGlzIHF1ZXN0aW9uIHdvdWxkICoqbm90KiogYmUgaW1tZWRpYXRlbHkgY2xvc2VkIGFzIHlvdSd2ZSBzdGF0ZWQ6IGUuZy4sIFsyNDk1IHZvdGVzXShodHRwOi8vc3RhY2tvdmVyZmxvdy5jb20vcXVlc3Rpb25zLzE5NDgxMi9saXN0LW9mLWZyZWVseS1hdmFpbGFibGUtcHJvZ3JhbW1pbmctYm9va3MpLCBbMTQ0MCB2b3Rlc10oaHR0cDovL3N0YWNrb3ZlcmZsb3cuY29tL3F1 2014-05-14T02:35:50.000+0000 36 22 8 WWVzLCB1c2luZyAxLW9mLW4gZW5jb2RpbmcgaXMgdmFsaWQgdG9vLg== 2014-05-14T06:47:00.000+0000 21 19 7 QSBuaWNlIGFydGljbGUgYWJvdXQgd2hlbiB5b3VyIGRhdGEgc3RhcnRzIHRvIGJlIHRvbyBiaWcgZm9yIG5vcm1hbCB1c2FnZSBjaHJpc3N0dWNjaGlvLmNvbS9ibG9nLzIwMTMvaGFkb29wX2hhdHJlZC5odG1s 2014-05-14T07:48:10.000+0000 115 14 0 QXMgdG8gdGhlIHNlY29uZCBwYXJ0IG9mIHlvdXIgcXVlc3Rpb24sIEkgaGF2ZSBwcm9wb3NlZCBhIGRpc2N1c3Npb24gaW4gbWV0YTogaHR0cDovL21ldGEuZGF0YXNjaWVuY2Uuc3RhY2tleGNoYW5nZS5jb20vcXVlc3Rpb25zLzUvc2hvdWxkLXdlLWFkb3B0LWEtc2VsZi1zdHVkeS10YWctbGlrZS1zdGF0cy1zZS1pbi1zY29wZS1hbmQtYXBwcm9hY2ggSG93IHRoYXQgZ2V0cyByZWNlaXZlZCBjb3VsZCBzaGFwZSB3aGV0aGVyIHlvdXIgcHJvZmljaWVuY3kgY29uY2VybiBpcyBhbnN3ZXJhYmxlIG9yIHdpdGhpbiBzY29wZS4= 2014-05-14T08:00:35.000+0000 53 31 1 V2hhdCBkbyB5b3UgbWVhbiB1bmRlciAiaW50ZXJlc3RpbmcgZ3JvdXBzIj8gRG8geW91IGhhdmUgc29tZSBwcmVkZWZpbmVkIGltcG9ydGFudCBmZWF0dXJlIGxpc3Q/ 2014-05-14T09:08:56.000+0000 120 31 0 SW50ZXJlc3RpbmcgZ3JvdXBzIGFyZSBhbnkgZ3JvdXBzIG9mIHNpemUgZ3JlYXRlciB0aGFuIHNvbWUgdGhyZXNob2xkIGFuIHRoYXQgYXJlIG11Y2ggYmlnZ2VyIHRoYW4gb3RoZXIgcG9zc2libGUgY2x1c3RlcnMu 2014-05-14T09:11:09.000+0000 118 31 1 SXQgaXNuJ3QgY2xlYXIgaG93IHlvdSB3aWxsIHBlcmZvcm0gcHJlcGFyZW1lbnQgc3RlcHMgb2YgeW91ciBkYXRhLiBCdXQgeW91IHNob3VsZCBsb29rIGF0IGFsZ29yaXRobXMgZGVzY3JpYmVkIGF0IGh0dHA6Ly9lbi53aWtpcGVkaWEub3JnL3dpa2kvQW5vbWFseV9kZXRlY3Rpb24gLiBJZiBJIHdlcmUgeW91LCBJJ3ZlIGNoZWNrZWQgU1ZNIG1ldGhvZCBmaXJzdA== 2014-05-14T09:31:01.000+0000 120 37 6 KzEgSSBwcmV0dHkgbXVjaCBhcHByZWNpYXRlIHRoZSBzdHJlc3Mgb3V0IG9uIGJpZyBkYXRhIGJlaW5nIG5vdCBhYm91dCAqd2hhdCBpcyB0aGUgc2l6ZSosIGFuZCByYXRoZXIgYWJvdXQgKndoYXQgaXMgdGhlIGNvbnRlbnQgKGNoYXJhY3RlcmlzdGljcyBvZikqLg== 2014-05-14T10:49:41.000+0000 84 51 0 RXhjZWxsZW50ISBBbnl0aGluZyBzaW1pbGFyIG9uIFdpbmRvd3M/IEkgc3VwcG9zZSBpZiBJIHdhbnQgdG8gY29uZGl0aW9uIGl0IG9uIHNvbWV0aGluZyBsaWtlIHRoZSBzaXplIG9mIHRoZSBkYXRhYmFzZSBJIGNhbiBoYXZlIG15IFIgc2NyaXB0IGNoZWNrIHRoYXQgYXQgdGhlIGJlZ2lubmluZyBhbmQgZWl0aGVyIHN0b3Agb3IgY29udGludWUgZ2VuZXJhdGluZyB0aGUgcmVwb3J0LiBXaGF0IGlmIEkgYWRkIHRoaXMgdG8gdGhlIGJlZ2lubmluZyBvZiB0aGUgUiBzY3JpcHQgYW5kIHRoZW4gSSB3YW50IHRvIHJ1biBpdCBl 2014-05-14T14:58:48.000+0000 151 51 1 QHJub3JiZXJnIFlvdSBjYW4gc2V0IGEgY3JvbiBqb2IgdG8gcmVwZWF0

Id ParentID PostTypeId CreationDate Score ViewCount Body OwnerUserId LastActivityDate Title Tags AnswerCount CommentCount FavoriteCount CloseDate 5 null 1 2014-05-13T23:58:30.000+0000 9 789 PHA+SSd2ZSBhbHdheXMgYmVlbiBpbnRlcmVzdGVkIGluIG1hY2hpbmUgbGVhcm5pbmcsIGJ1dCBJIGNhbid0IGZpZ3VyZSBvdXQgb25lIHRoaW5nIGFib3V0IHN0YXJ0aW5nIG91dCB3aXRoIGEgc2ltcGxlICJIZWxsbyBXb3JsZCIgZXhhbXBsZSAtIGhvdyBjYW4gSSBhdm9pZCBoYXJkLWNvZGluZyBiZWhhdmlvcj88L3A+JiN4QTsmI3hBOzxwPkZvciBleGFtcGxlLCBpZiBJIHdhbnRlZCB0byAidGVhY2giIGEgYm90IGhvdyB0byBhdm9pZCByYW5kb21seSBwbGFjZWQgb2JzdGFjbGVzLCBJIGNvdWxkbid0IGp1c3QgdXNlIHJlbGF0aXZlIG1vdGlvbiwgYmVjYXVzZSB0aGUgb2JzdGFjbGVzIG1vdmUgYXJvdW5kLCBidXQgSSBkb24ndCB3YW50IHRvIGhhcmQgY29kZSwgc2F5LCBkaXN0YW5jZSwgYmVjYXVzZSB0aGF0IHJ1aW5zIHRoZSB3aG9sZSBwb2ludCBvZiBtYWNoaW5lIGxlYXJuaW5nLjwvcD4mI3hBOyYjeEE7PHA+T2J2aW91c2x5LCByYW5kb21seSBnZW5lcmF0aW5nIGNvZGUgd291bGQgYmUgaW1wcmFjdGljYWwsIHNvIGhvdyBjb3VsZCBJIGRvIHRoaXM/PC9wPiYjeEE7 5 2014-05-14T00:36:31.000+0000 SG93IGNhbiBJIGRvIHNpbXBsZSBtYWNoaW5lIGxlYXJuaW5nIHdpdGhvdXQgaGFyZC1jb2RpbmcgYmVoYXZpb3I/ 1 1 1 2014-05-14T14:40:25.000+0000 7 null 1 2014-05-14T00:11:06.000+0000 4 459 PHA+QXMgYSByZXNlYXJjaGVyIGFuZCBpbnN0cnVjdG9yLCBJJ20gbG9va2luZyBmb3Igb3Blbi1zb3VyY2UgYm9va3MgKG9yIHNpbWlsYXIgbWF0ZXJpYWxzKSB0aGF0IHByb3ZpZGUgYSByZWxhdGl2ZWx5IHRob3JvdWdoIG92ZXJ2aWV3IG9mIGRhdGEgc2NpZW5jZSBmcm9tIGFuIGFwcGxpZWQgcGVyc3BlY3RpdmUuIFRvIGJlIGNsZWFyLCBJJ20gZXNwZWNpYWxseSBpbnRlcmVzdGVkIGluIGEgdGhvcm91Z2ggb3ZlcnZpZXcgdGhhdCBwcm92aWRlcyBtYXRlcmlhbCBzdWl0YWJsZSBmb3IgYSBjb2xsZWdlLWxldmVsIGNvdXJzZSwgbm90IHBhcnRpY3VsYXIgcGllY2VzIG9yIHBhcGVycy48L3A+JiN4QTs= 36 2014-05-16T13:45:00.000+0000 V2hhdCBvcGVuLXNvdXJjZSBib29rcyAob3Igb3RoZXIgbWF0ZXJpYWxzKSBwcm92aWRlIGEgcmVsYXRpdmVseSB0aG9yb3VnaCBvdmVydmlldyBvZiBkYXRhIHNjaWVuY2U/ 3 4 1 2014-05-14T08:40:54.000+0000 9 5 2 2014-05-14T00:36:31.000+0000 5 0 PHA+Tm90IHN1cmUgaWYgdGhpcyBmaXRzIHRoZSBzY29wZSBvZiB0aGlzIFNFLCBidXQgaGVyZSdzIGEgc3RhYiBhdCBhbiBhbnN3ZXIgYW55d2F5LjwvcD4mI3hBOyYjeEE7PHA+V2l0aCBhbGwgQUkgYXBwcm9hY2hlcyB5b3UgaGF2ZSB0byBkZWNpZGUgd2hhdCBpdCBpcyB5b3UncmUgbW9kZWxsaW5nIGFuZCB3aGF0IGtpbmQgb2YgdW5jZXJ0YWludHkgdGhlcmUgaXMuIE9uY2UgeW91IHBpY2sgYSBmcmFtZXdvcmsgdGhhdCBhbGxvd3MgbW9kZWxsaW5nIG9mIHlvdXIgc2l0dWF0aW9uLCB5b3UgdGhlbiBzZWUgd2hpY2ggZWxlbWVudHMgYXJlICJmaXhlZCIgYW5kIHdoaWNoIGFyZSBmbGV4aWJsZS4gRm9yIGV4YW1wbGUsIHRoZSBtb2RlbCBtYXkgYWxsb3cgeW91IHRvIGRlZmluZSB5b3VyIG93biBuZXR3b3JrIHN0cnVjdHVyZSAob3IgZXZlbiBsZWFybiBpdCkgd2l0aCBjZXJ0YWluIGNvbnN0cmFpbnRzLiBZb3UgaGF2ZSB0byBkZWNpZGUgd2hldGhlciB0aGlzIGZsZXhpYmlsaXR5IGlzIHN1ZmZpY2llbnQgZm9yIHlvdXIgcHVycG9zZXMuIFRoZW4gd2l0aGluIGEgcGFydGljdWxhciBuZXR3b3JrIHN0cnVjdHVyZSwgeW91IGNhbiBsZWFybiBwYXJhbWV0ZXJzIGdpdmVuIGEgc3BlY2lmaWMgdHJhaW5pbmcgZGF0YXNldC48L3A+JiN4QTsmI3hBOzxwPllvdSByYXJlbHkgaGFyZC1jb2RlIGJlaGF2aW9yIGluIEFJL01MIHNvbHV0aW9ucy4gSXQncyBhbGwgYWJvdXQgbW9kZWxsaW5nIHRoZSB1bmRlcmx5aW5nIHNpdHVhdGlvbiBhbmQgYWNjb21tb2RhdGluZyBkaWZmZXJlbnQgc2l0dWF0aW9ucyBieSB0d2Vha2luZyBlbGVtZW50cyBvZiB0aGUgbW9kZWwuPC9wPiYjeEE7JiN4QTs8cD5JbiB5b3VyIGV4YW1wbGUsIHBlcmhhcHMgeW91IG1pZ2h0IGhhdmUgdGhlIHJvYm90IGxlYXJuIGhvdyB0byBkZXRlY3Qgb2JzdGFjbGVzIChieSBhbmFseXppbmcgZWxlbWVudHMgaW4gdGhlIGVudmlyb25tZW50KSwgb3IgeW91IG1pZ2h0IGhhdmUgaXQga2VlcCB0cmFjayBvZiB3aGVyZSB0aGUgb2JzdGFjbGVzIHdlcmUgYW5kIHdoaWNoIHdheSB0aGV5IHdlcmUgbW92aW5nLjwvcD4mI3hBOw== 51 2014-05-14T00:36:31.000+0000 null null 0 0 0 null 10 7 2 2014-05-14T00:53:43.000+0000 13 0 PHA+T25lIGJvb2sgdGhhdCdzIGZyZWVseSBhdmFpbGFibGUgaXMgIlRoZSBFbGVtZW50cyBvZiBTdGF0aXN0aWNhbCBMZWFybmluZyIgYnkgSGFzdGllLCBUaWJzaGlyYW5pLCBhbmQgRnJpZWRtYW4gKHB1Ymxpc2hlZCBieSBTcHJpbmdlcik6IDxhIGhyZWY9Imh0dHA6Ly9zdGF0d2ViLnN0YW5mb3JkLmVkdS9+dGlicy9FbGVtU3RhdExlYXJuLyI+c2VlIFRpYnNoaXJhbmkncyB3ZWJzaXRlPC9hPi48L3A+JiN4QTsmI3hBOzxwPkFub3RoZXIgZmFudGFzdGljIHNvdXJjZSwgYWx0aG91Z2ggaXQgaXNuJ3QgYSBib29rLCBpcyBBbmRyZXcgTmcncyBNYWNoaW5lIExlYXJuaW5nIGNvdXJzZSBvbiBDb3Vyc2VyYS4gVGhpcyBoYXMgYSBtdWNoIG1vcmUgYXBwbGllZC1mb2N1cyB0aGFuIHRoZSBhYm92ZSBib29rLCBhbmQgUHJvZi4gTmcgZG9lcyBhIGdyZWF0IGpvYiBvZiBleHBsYWluaW5nIHRoZSB0aGlua2luZyBiZWhpbmQgc2V2ZXJhbCBkaWZ

Id Reputation CreationDate DisplayName LastAccessDate AboutMe Views UpVotes DownVotes -1 1 2014-05-13T21:29:22.000+0000 Community 2014-05-13T21:29:22.000+0000 Hi, I'm not really a person. 

 I'm a background process that helps keep this site clean! 

 I do things like 

 
 Randomly poke old unanswered questions every hour so they get some attention 
 Own community questions and answers so nobody 3 819 1575 1 101 2014-05-13T22:58:54.000+0000 Adam Lear 2020-09-30T19:08:29.000+0000 
 Developer at Stack Overflow focusing on public Q&A. Russian Canadian working in the American idiom. 
 Once upon a time: 
 
 community manager at Stack Overflow 
 elected moderator on Stack Overflow and Software Engineering 
 desktop softwar 713 0 0 2 101 2014-05-13T22:59:19.000+0000 Geoff Dalgas 2019-09-03T19:10:22.000+0000 " Developer on the Stack Overflow team. Find me on 

 Twitter 
 
 Stack Overflow Valued Associate #000" 9 0 0 3 101 2014-05-13T23:15:34.000+0000 hichris123 2020-06-29T16:52:58.000+0000 " I'm a student interested in technology. 

 Also an Earth Science moderator. Come check us out! 
" 8 1 3 4 101 2014-05-13T23:16:09.000+0000 Ben Collins 2014-08-04T15:25:54.000+0000 " I work with Olo solving problems for people who want to order food online. I'm also a Stack Overflow alumnus and Microsoft alumnus. 

 I l" 9 0 0 5 215 2014-05-13T23:16:11.000+0000 Doorknob 2020-04-23T18:35:59.000+0000 "

 https://tck.mn 

 Elected moderator ♦ on Code Golf . 

 Email andy@tck.mn or find me in chat: The" 28 1 2 6 101 2014-05-13T23:16:26.000+0000 gerrit 2020-02-26T13:11:32.000+0000 I'm a researcher in satellite remote sensing at the Deutscher Wetterdienst in Offenbach, Hessen, Germany. I first came to Stack Exchange for practical reasons: Tex.SE has been of major help when I wrote my licentiate thesis. Since then, I have discovered the joy of many websites. As my network 12 13 1 7 101 2014-05-13T23:17:05.000+0000 Undo 2020-07-01T01:25:00.000+0000 " Stack Overflow moderator. I bite, but only when sufficiently provoked. 

 Everything I post on Stack Overflow is licensed to you under CC0 : 

 4 2 1 8 101 2014-05-13T23:17:26.000+0000 Jon Ericson 2019-06-04T19:18:36.000+0000 " Community Product & Operations Manager for College Confidential . 

 Stack Exchange no longer employs me as a 2 0 0 9 1102 2014-05-13T23:18:21.000+0000 rolfl 2020-07-07T12:23:34.000+0000 " Maintainer of the JDOM Open Source Java XML library. 
" 34 2 0 10 101 2014-05-13T23:18:31.000+0000 Dave Kincaid 2020-10-16T14:03:49.000+0000 Working as a Associate Fellow in Data Science at IDEXX Laboratories and a doctoral candidate in Biomedical Informatics and Computational Biology at University of Minnesota. 
 4 1 0 11 213 2014-05-13T23:20:53.000+0000 Yavar 2020-11-23T22:56:16.000+0000 I design Algorithms and construct Data Structures for Search, Information Retrieval & Machine Learning. 
 13 10 0 12 101 2014-05-13T23:21:22.000+0000 hairboat 2018-04-02T21:34:06.000+0000 " I work for our Stack Overflow overlords, helping folks learn how to decide what to have for lunch. If you have a recommendation you'd like to share, you can email me at abby@stackoverflow.com. 

 1 0 0 14 2782 2014-05-13T23:24:41.000+0000 Tim Goodman 2020-06-19T16:11:57.000+0000 NULL 143 33 0 15 101 2014-05-13T23:25:18.000+0000 Tony Boyles 2020-11-11T19:10:45.000+0000 NULL 1 3 0 16 1 2014-05-13T23:25:24.000+0000 Jeremy 2018-05-27T23:02:29.000+0000 . 
 1 0 0 17 236 2014-05-13T23:25:26.000+0000 Dr. Snoopy 2020-10-27T22:38:42.000+0000 Researcher @ German Research Center for Artificial Intelligence, Robotics Innovation Center. 
 6 0 0 18 101 2014-05-13T23:27:57.000+0000 Gilles 'SO- stop being evil' 2020-07-13T19:04:23.000+0000 " Help defend Monica from defamation ! 

 Stack Overflow, Inc. must 1 12 2 19 101 2014-05-13T23:29:01.000+0000 Max Ionov 2019-06-12T15:11:55.000+0000 NULL 1 3 0 20 101 2014-05-13T23:30:33.000+0000 TheDoctor 2014-05-14T21:41:38.000+0000 Timelord doge with Pythonic superpowers. 

 Contact: nwx{at}protonmail.com 


Id Reputation CreationDate DisplayName LastAccessDate AboutMe Views UpVotes DownVotes -1 1 2014-05-13T21:29:22.000+0000 Community 2014-05-13T21:29:22.000+0000 Hi, I'm not really a person. 

 I'm a background process that helps keep this site clean! 

 I do things like 

 
 Randomly poke old unanswered questions every hour so they get some attention 
 Own community questions and answers so nobody 3 819 1575 1 101 2014-05-13T22:58:54.000+0000 Adam Lear 2020-09-30T19:08:29.000+0000 
 Developer at Stack Overflow focusing on public Q&A. Russian Canadian working in the American idiom. 
 Once upon a time: 
 
 community manager at Stack Overflow 
 elected moderator on Stack Overflow and Software Engineering 
 desktop softwar 713 0 0 2 101 2014-05-13T22:59:19.000+0000 Geoff Dalgas 2019-09-03T19:10:22.000+0000 " Developer on the Stack Overflow team. Find me on 

 Twitter 
 
 Stack Overflow Valued Associate #000" 9 0 0 3 101 2014-05-13T23:15:34.000+0000 hichris123 2020-06-29T16:52:58.000+0000 " I'm a student interested in technology. 

 Also an Earth Science moderator. Come check us out! 
" 8 1 3 4 101 2014-05-13T23:16:09.000+0000 Ben Collins 2014-08-04T15:25:54.000+0000 " I work with Olo solving problems for people who want to order food online. I'm also a Stack Overflow alumnus and Microsoft alumnus. 

 I l" 9 0 0 5 215 2014-05-13T23:16:11.000+0000 Doorknob 2020-04-23T18:35:59.000+0000 "

 https://tck.mn 

 Elected moderator ♦ on Code Golf . 

 Email andy@tck.mn or find me in chat: The" 28 1 2 6 101 2014-05-13T23:16:26.000+0000 gerrit 2020-02-26T13:11:32.000+0000 I'm a researcher in satellite remote sensing at the Deutscher Wetterdienst in Offenbach, Hessen, Germany. I first came to Stack Exchange for practical reasons: Tex.SE has been of major help when I wrote my licentiate thesis. Since then, I have discovered the joy of many websites. As my network 12 13 1 7 101 2014-05-13T23:17:05.000+0000 Undo 2020-07-01T01:25:00.000+0000 " Stack Overflow moderator. I bite, but only when sufficiently provoked. 

 Everything I post on Stack Overflow is licensed to you under CC0 : 

 4 2 1 8 101 2014-05-13T23:17:26.000+0000 Jon Ericson 2019-06-04T19:18:36.000+0000 " Community Product & Operations Manager for College Confidential . 

 Stack Exchange no longer employs me as a 2 0 0 9 1102 2014-05-13T23:18:21.000+0000 rolfl 2020-07-07T12:23:34.000+0000 " Maintainer of the JDOM Open Source Java XML library. 
" 34 2 0 10 101 2014-05-13T23:18:31.000+0000 Dave Kincaid 2020-10-16T14:03:49.000+0000 Working as a Associate Fellow in Data Science at IDEXX Laboratories and a doctoral candidate in Biomedical Informatics and Computational Biology at University of Minnesota. 
 4 1 0 11 213 2014-05-13T23:20:53.000+0000 Yavar 2020-11-23T22:56:16.000+0000 I design Algorithms and construct Data Structures for Search, Information Retrieval & Machine Learning. 
 13 10 0 12 101 2014-05-13T23:21:22.000+0000 hairboat 2018-04-02T21:34:06.000+0000 " I work for our Stack Overflow overlords, helping folks learn how to decide what to have for lunch. If you have a recommendation you'd like to share, you can email me at abby@stackoverflow.com. 

 1 0 0 14 2782 2014-05-13T23:24:41.000+0000 Tim Goodman 2020-06-19T16:11:57.000+0000 NULL 143 33 0 15 101 2014-05-13T23:25:18.000+0000 Tony Boyles 2020-11-11T19:10:45.000+0000 NULL 1 3 0 16 1 2014-05-13T23:25:24.000+0000 Jeremy 2018-05-27T23:02:29.000+0000 . 
 1 0 0 17 236 2014-05-13T23:25:26.000+0000 Dr. Snoopy 2020-10-27T22:38:42.000+0000 Researcher @ German Research Center for Artificial Intelligence, Robotics Innovation Center. 
 6 0 0 18 101 2014-05-13T23:27:57.000+0000 Gilles 'SO- stop being evil' 2020-07-13T19:04:23.000+0000 " Help defend Monica from defamation ! 

 Stack Overflow, Inc. must 1 12 2 19 101 2014-05-13T23:29:01.000+0000 Max Ionov 2019-06-12T15:11:55.000+0000 NULL 1 3 0 20 101 2014-05-13T23:30:33.000+0000 TheDoctor 2014-05-14T21:41:38.000+0000 Timelord doge with Pythonic superpowers. 

 Contact: nwx{at}protonmail.com 


UserId Name Date Class 1 Informed 2014-05-13T23:06:44.000+0000 3 2 Autobiographer 2014-05-13T23:11:04.000+0000 3 4 Autobiographer 2014-05-13T23:20:53.000+0000 3 5 Autobiographer 2014-05-13T23:20:53.000+0000 3 8 Autobiographer 2014-05-13T23:20:53.000+0000 3 9 Autobiographer 2014-05-13T23:20:53.000+0000 3 11 Autobiographer 2014-05-13T23:25:53.000+0000 3 12 Autobiographer 2014-05-13T23:25:53.000+0000 3 17 Autobiographer 2014-05-13T23:25:53.000+0000 3 3 Informed 2014-05-13T23:27:23.000+0000 3 14 Informed 2014-05-13T23:27:35.000+0000 3 22 Autobiographer 2014-05-13T23:40:53.000+0000 3 24 Autobiographer 2014-05-13T23:40:53.000+0000 3 24 Informed 2014-05-13T23:41:05.000+0000 3 28 Autobiographer 2014-05-13T23:50:54.000+0000 3 29 Autobiographer 2014-05-13T23:50:54.000+0000 3 30 Autobiographer 2014-05-13T23:50:54.000+0000 3 6 Student 2014-05-13T23:50:54.000+0000 3 29 Supporter 2014-05-13T23:50:54.000+0000 3 32 Autobiographer 2014-05-13T23:55:57.000+0000 3 34 Autobiographer 2014-05-13T23:55:57.000+0000 3 35 Autobiographer 2014-05-13T23:55:57.000+0000 3 38 Autobiographer 2014-05-13T23:55:57.000+0000 3 37 Supporter 2014-05-13T23:55:57.000+0000 3 26 Editor 2014-05-14T00:00:58.000+0000 3 26 Supporter 2014-05-14T00:00:58.000+0000 3 38 Supporter 2014-05-14T00:00:58.000+0000 3 26 Teacher 2014-05-14T00:00:58.000+0000 3 36 Teacher 2014-05-14T00:00:58.000+0000 3 7 Citizen Patrol 2014-05-14T00:05:26.000+0000 3 5 Student 2014-05-14T00:05:58.000+0000 3 19 Supporter 2014-05-14T00:05:58.000+0000 3 41 Autobiographer 2014-05-14T00:12:25.000+0000 3 37 Precognitive 2014-05-14T00:12:25.000+0000 3 14 Precognitive 2014-05-14T00:12:25.000+0000 3 17 Precognitive 2014-05-14T00:12:25.000+0000 3 10 Precognitive 2014-05-14T00:12:25.000+0000 3 15 Precognitive 2014-05-14T00:12:25.000+0000 3 11 Precognitive 2014-05-14T00:12:25.000+0000 3 25 Precognitive 2014-05-14T00:12:25.000+0000 3 31 Precognitive 2014-05-14T00:12:25.000+0000 3 20 Precognitive 2014-05-14T00:12:25.000+0000 3 36 Student 2014-05-14T00:12:25.000+0000 3 3 Supporter 2014-05-14T00:12:25.000+0000 3 36 Supporter 2014-05-14T00:17:25.000+0000 3 34 Teacher 2014-05-14T00:17:25.000+0000 3 20 Supporter 2014-05-14T00:22:26.000+0000 3 46 Autobiographer 2014-05-14T00:27:25.000+0000 3 53 Autobiographer 2014-05-14T00:37:25.000+0000 3 51 Supporter 2014-05-14T00:37:25.000+0000 3 51 Citizen Patrol 2014-05-14T00:39:24.000+0000 3 55 Autobiographer 2014-05-14T00:49:48.000+0000 3 46 Student 2014-05-14T00:54:48.000+0000 3 22 Supporter 2014-05-14T00:54:48.000+0000 3 22 Teacher 2014-05-14T00:54:48.000+0000 3 51 Teacher 2014-05-14T00:54:48.000+0000 3 61 Autobiographer 2014-05-14T00:59:49.000+0000 3 62 Autobiographer 2014-05-14T00:59:49.000+0000 3 22 Citizen Patrol 2014-05-14T00:58:13.000+0000 3 9 Quorum 2014-05-14T01:12:25.000+0000 3 55 Precognitive 2014-05-14T01:12:25.000+0000 3 43 Precognitive 2014-05-14T01:12:25.000+0000 3 52 Precognitive 2014-05-14T01:12:25.000+0000 3 62 Precognitive 2014-05-14T01:12:25.000+0000 3 48 Precognitive 2014-05-14T01:12:25.000+0000 3 63 Precognitive 2014-05-14T01:12:25.000+0000 3 64 Precognitive 2014-05-14T01:12:25.000+0000 3 9 Talkative 2014-05-14T01:12:25.000+0000 3 66 Informed 2014-05-14T01:19:21.000+0000 3 66 Autobiographer 2014-05-14T01:19:49.000+0000 3 38 Citizen Patrol 2014-05-14T01:19:03.000+0000 3 64 Supporter 2014-05-14T01:19:49.000+0000 3 66 Supporter 2014-05-14T01:19:49.000+0000 3 66 Student 2014-05-14T01:34:49.000+0000 3 64 Informed 2014-05-14T01:35:57.000+0000 3 70 Informed 2014-05-14T01:50:35.000+0000 3 5 Informed 2014-05-14T01:55:55.000+0000 3 72 Autobiographer 2014-05-14T01:56:33.000+0000 3 73 Autobiographer 2014-05-14T01:56:33.000+0000 3 3 Critic 2014-05-14T01:56:33.000+0000 3 5 Critic 2014-05-14T01:56:33.000+0000 3 7 Critic 2014-05-14T01:56:33.000+0000 3 20 Critic 2014-05-14T01:56:33.000+0000 3 22 Critic 2014-05-14T01:56:33.000+0000 3 36 Critic 2014-05-14T01:56:33.000+0000 3 38 Critic 2014-05-14T01:56:33.000+0000 3 48 Critic 2014-05-14T01:56:33.000+0000 3 50 Critic 2014-05-14T01:56

PostId Score Text CreationDate UserId 5 9 dGhpcyBpcyBhIHN1cGVyIHRoZW9yZXRpY2FsIEFJIHF1ZXN0aW9uLiBBbiBpbnRlcmVzdGluZyBkaXNjdXNzaW9uISBidXQgb3V0IG9mIHBsYWNlLi4u 2014-05-14T00:23:15.000+0000 34 7 4 TGlzdCBxdWVzdGlvbnMgYXJlIHVzdWFsbHkgbm90IHN1aXRlZCBmb3IgU3RhY2sgRXhjaGFuZ2Ugd2Vic2l0ZXMgc2luY2UgdGhlcmUgaXNuJ3QgYW4gIm9iamVjdGl2ZSIgYW5zd2VyIG9yIGEgd2F5IHRvIG1lYXN1cmUgdGhlIHVzZWZ1bG5lc3Mgb2YgYW4gYW5zd2VyLiBIYXZpbmcgc2FpZCB0aGF0LCBvbmUgb2YgbXkgcmVjb21tZW5kYXRpb25zIHdvdWxkIGJlIE1hY0theSdzICJJbmZvcm1hdGlvbiBUaGVvcnksIEluZmVyZW5jZSwgYW5kIExlYXJuaW5nIEFsZ29yaXRobXMuIg== 2014-05-14T00:38:19.000+0000 51 7 3 VGhpcyBxdWVzdGlvbiBhcHBlYXJzIHRvIGJlIG9mZi10b3BpYyBiZWNhdXNlIGl0IGlzIGFza3MgZm9yIGEgZmF2b3JpdGUgcmVzb3VyY2UuICBPbiBvdGhlciBTRSBzaXRlcywgdGhpcyB3b3VsZCBpbW1lZGlhdGVseSBiZSBjbG9zZWQuICBTaW5jZSB0aGlzIGlzIGEgbmV3IHNpdGUsIHdlIHN0aWxsIGhhdmUgdG8gZGVjaWRlIGlmIHRoaXMgaXMgYSB2YWxpZCBxdWVzdGlvbiBoZXJl 2014-05-14T01:16:12.000+0000 66 15 3 VGhpcyBxdWVzdGlvbiBpcyBmYXIgdG9vIGJyb2FkLiBJdCBtYXkgYmUgc2FsdmFnZWQgYnkgcmVzdHJpY3RpbmcgdGhlIHF1ZXN0aW9uIHRvIGEgcGFydGljdWxhciB1c2UgY2FzZS4= 2014-05-14T02:00:22.000+0000 51 10 2 TmljZSBvbmUsIEBOaWNob2xhcy4uLiBBbm90aGVyIGJvb2sgZnJvbSBIYXN0aWUgYW5kIFRpYnNoaXJhbmkgaXMgW0ludHJvZHVjdGlvbiB0byBTdGF0aXN0aWNhbCBMZWFybmluZ10oaHR0cDovL3d3dy1iY2YudXNjLmVkdS9+Z2FyZXRoL0lTTC8pLCB3aGljaCBpcyBhIGJpdCBnZW50bGVyIG9mIGFuIGVudHJ5IGNvbXBhcmVkIHRvIEVTTC4= 2014-05-14T02:16:20.000+0000 24 7 0 RmFpciBlbm91Z2ggcmVnYXJkaW5nIHdoYXQgY29uc3RpdHV0ZXMgYSAidmFsaWQiIHF1ZXN0aW9uLCBhbHRob3VnaCBvbiBvdGhlciBTRSBzaXRlcyB0aGlzIHF1ZXN0aW9uIHdvdWxkICoqbm90KiogYmUgaW1tZWRpYXRlbHkgY2xvc2VkIGFzIHlvdSd2ZSBzdGF0ZWQ6IGUuZy4sIFsyNDk1IHZvdGVzXShodHRwOi8vc3RhY2tvdmVyZmxvdy5jb20vcXVlc3Rpb25zLzE5NDgxMi9saXN0LW9mLWZyZWVseS1hdmFpbGFibGUtcHJvZ3JhbW1pbmctYm9va3MpLCBbMTQ0MCB2b3Rlc10oaHR0cDovL3N0YWNrb3ZlcmZsb3cuY29tL3F1 2014-05-14T02:35:50.000+0000 36 22 8 WWVzLCB1c2luZyAxLW9mLW4gZW5jb2RpbmcgaXMgdmFsaWQgdG9vLg== 2014-05-14T06:47:00.000+0000 21 19 7 QSBuaWNlIGFydGljbGUgYWJvdXQgd2hlbiB5b3VyIGRhdGEgc3RhcnRzIHRvIGJlIHRvbyBiaWcgZm9yIG5vcm1hbCB1c2FnZSBjaHJpc3N0dWNjaGlvLmNvbS9ibG9nLzIwMTMvaGFkb29wX2hhdHJlZC5odG1s 2014-05-14T07:48:10.000+0000 115 14 0 QXMgdG8gdGhlIHNlY29uZCBwYXJ0IG9mIHlvdXIgcXVlc3Rpb24sIEkgaGF2ZSBwcm9wb3NlZCBhIGRpc2N1c3Npb24gaW4gbWV0YTogaHR0cDovL21ldGEuZGF0YXNjaWVuY2Uuc3RhY2tleGNoYW5nZS5jb20vcXVlc3Rpb25zLzUvc2hvdWxkLXdlLWFkb3B0LWEtc2VsZi1zdHVkeS10YWctbGlrZS1zdGF0cy1zZS1pbi1zY29wZS1hbmQtYXBwcm9hY2ggSG93IHRoYXQgZ2V0cyByZWNlaXZlZCBjb3VsZCBzaGFwZSB3aGV0aGVyIHlvdXIgcHJvZmljaWVuY3kgY29uY2VybiBpcyBhbnN3ZXJhYmxlIG9yIHdpdGhpbiBzY29wZS4= 2014-05-14T08:00:35.000+0000 53 31 1 V2hhdCBkbyB5b3UgbWVhbiB1bmRlciAiaW50ZXJlc3RpbmcgZ3JvdXBzIj8gRG8geW91IGhhdmUgc29tZSBwcmVkZWZpbmVkIGltcG9ydGFudCBmZWF0dXJlIGxpc3Q/ 2014-05-14T09:08:56.000+0000 120 31 0 SW50ZXJlc3RpbmcgZ3JvdXBzIGFyZSBhbnkgZ3JvdXBzIG9mIHNpemUgZ3JlYXRlciB0aGFuIHNvbWUgdGhyZXNob2xkIGFuIHRoYXQgYXJlIG11Y2ggYmlnZ2VyIHRoYW4gb3RoZXIgcG9zc2libGUgY2x1c3RlcnMu 2014-05-14T09:11:09.000+0000 118 31 1 SXQgaXNuJ3QgY2xlYXIgaG93IHlvdSB3aWxsIHBlcmZvcm0gcHJlcGFyZW1lbnQgc3RlcHMgb2YgeW91ciBkYXRhLiBCdXQgeW91IHNob3VsZCBsb29rIGF0IGFsZ29yaXRobXMgZGVzY3JpYmVkIGF0IGh0dHA6Ly9lbi53aWtpcGVkaWEub3JnL3dpa2kvQW5vbWFseV9kZXRlY3Rpb24gLiBJZiBJIHdlcmUgeW91LCBJJ3ZlIGNoZWNrZWQgU1ZNIG1ldGhvZCBmaXJzdA== 2014-05-14T09:31:01.000+0000 120 37 6 KzEgSSBwcmV0dHkgbXVjaCBhcHByZWNpYXRlIHRoZSBzdHJlc3Mgb3V0IG9uIGJpZyBkYXRhIGJlaW5nIG5vdCBhYm91dCAqd2hhdCBpcyB0aGUgc2l6ZSosIGFuZCByYXRoZXIgYWJvdXQgKndoYXQgaXMgdGhlIGNvbnRlbnQgKGNoYXJhY3RlcmlzdGljcyBvZikqLg== 2014-05-14T10:49:41.000+0000 84 51 0 RXhjZWxsZW50ISBBbnl0aGluZyBzaW1pbGFyIG9uIFdpbmRvd3M/IEkgc3VwcG9zZSBpZiBJIHdhbnQgdG8gY29uZGl0aW9uIGl0IG9uIHNvbWV0aGluZyBsaWtlIHRoZSBzaXplIG9mIHRoZSBkYXRhYmFzZSBJIGNhbiBoYXZlIG15IFIgc2NyaXB0IGNoZWNrIHRoYXQgYXQgdGhlIGJlZ2lubmluZyBhbmQgZWl0aGVyIHN0b3Agb3IgY29udGludWUgZ2VuZXJhdGluZyB0aGUgcmVwb3J0LiBXaGF0IGlmIEkgYWRkIHRoaXMgdG8gdGhlIGJlZ2lubmluZyBvZiB0aGUgUiBzY3JpcHQgYW5kIHRoZW4gSSB3YW50IHRvIHJ1biBpdCBl 2014-05-14T14:58:48.000+0000 151 51 1 QHJub3JiZXJnIFlvdSBjYW4gc2V0IGEgY3JvbiBqb2IgdG8gcmVwZWF0

Id ParentID PostTypeId CreationDate Score ViewCount Body OwnerUserId LastActivityDate Title Tags AnswerCount CommentCount FavoriteCount CloseDate 5 null 1 2014-05-13T23:58:30.000+0000 9 789 PHA+SSd2ZSBhbHdheXMgYmVlbiBpbnRlcmVzdGVkIGluIG1hY2hpbmUgbGVhcm5pbmcsIGJ1dCBJIGNhbid0IGZpZ3VyZSBvdXQgb25lIHRoaW5nIGFib3V0IHN0YXJ0aW5nIG91dCB3aXRoIGEgc2ltcGxlICJIZWxsbyBXb3JsZCIgZXhhbXBsZSAtIGhvdyBjYW4gSSBhdm9pZCBoYXJkLWNvZGluZyBiZWhhdmlvcj88L3A+JiN4QTsmI3hBOzxwPkZvciBleGFtcGxlLCBpZiBJIHdhbnRlZCB0byAidGVhY2giIGEgYm90IGhvdyB0byBhdm9pZCByYW5kb21seSBwbGFjZWQgb2JzdGFjbGVzLCBJIGNvdWxkbid0IGp1c3QgdXNlIHJlbGF0aXZlIG1vdGlvbiwgYmVjYXVzZSB0aGUgb2JzdGFjbGVzIG1vdmUgYXJvdW5kLCBidXQgSSBkb24ndCB3YW50IHRvIGhhcmQgY29kZSwgc2F5LCBkaXN0YW5jZSwgYmVjYXVzZSB0aGF0IHJ1aW5zIHRoZSB3aG9sZSBwb2ludCBvZiBtYWNoaW5lIGxlYXJuaW5nLjwvcD4mI3hBOyYjeEE7PHA+T2J2aW91c2x5LCByYW5kb21seSBnZW5lcmF0aW5nIGNvZGUgd291bGQgYmUgaW1wcmFjdGljYWwsIHNvIGhvdyBjb3VsZCBJIGRvIHRoaXM/PC9wPiYjeEE7 5 2014-05-14T00:36:31.000+0000 SG93IGNhbiBJIGRvIHNpbXBsZSBtYWNoaW5lIGxlYXJuaW5nIHdpdGhvdXQgaGFyZC1jb2RpbmcgYmVoYXZpb3I/ 1 1 1 2014-05-14T14:40:25.000+0000 7 null 1 2014-05-14T00:11:06.000+0000 4 459 PHA+QXMgYSByZXNlYXJjaGVyIGFuZCBpbnN0cnVjdG9yLCBJJ20gbG9va2luZyBmb3Igb3Blbi1zb3VyY2UgYm9va3MgKG9yIHNpbWlsYXIgbWF0ZXJpYWxzKSB0aGF0IHByb3ZpZGUgYSByZWxhdGl2ZWx5IHRob3JvdWdoIG92ZXJ2aWV3IG9mIGRhdGEgc2NpZW5jZSBmcm9tIGFuIGFwcGxpZWQgcGVyc3BlY3RpdmUuIFRvIGJlIGNsZWFyLCBJJ20gZXNwZWNpYWxseSBpbnRlcmVzdGVkIGluIGEgdGhvcm91Z2ggb3ZlcnZpZXcgdGhhdCBwcm92aWRlcyBtYXRlcmlhbCBzdWl0YWJsZSBmb3IgYSBjb2xsZWdlLWxldmVsIGNvdXJzZSwgbm90IHBhcnRpY3VsYXIgcGllY2VzIG9yIHBhcGVycy48L3A+JiN4QTs= 36 2014-05-16T13:45:00.000+0000 V2hhdCBvcGVuLXNvdXJjZSBib29rcyAob3Igb3RoZXIgbWF0ZXJpYWxzKSBwcm92aWRlIGEgcmVsYXRpdmVseSB0aG9yb3VnaCBvdmVydmlldyBvZiBkYXRhIHNjaWVuY2U/ 3 4 1 2014-05-14T08:40:54.000+0000 9 5 2 2014-05-14T00:36:31.000+0000 5 0 PHA+Tm90IHN1cmUgaWYgdGhpcyBmaXRzIHRoZSBzY29wZSBvZiB0aGlzIFNFLCBidXQgaGVyZSdzIGEgc3RhYiBhdCBhbiBhbnN3ZXIgYW55d2F5LjwvcD4mI3hBOyYjeEE7PHA+V2l0aCBhbGwgQUkgYXBwcm9hY2hlcyB5b3UgaGF2ZSB0byBkZWNpZGUgd2hhdCBpdCBpcyB5b3UncmUgbW9kZWxsaW5nIGFuZCB3aGF0IGtpbmQgb2YgdW5jZXJ0YWludHkgdGhlcmUgaXMuIE9uY2UgeW91IHBpY2sgYSBmcmFtZXdvcmsgdGhhdCBhbGxvd3MgbW9kZWxsaW5nIG9mIHlvdXIgc2l0dWF0aW9uLCB5b3UgdGhlbiBzZWUgd2hpY2ggZWxlbWVudHMgYXJlICJmaXhlZCIgYW5kIHdoaWNoIGFyZSBmbGV4aWJsZS4gRm9yIGV4YW1wbGUsIHRoZSBtb2RlbCBtYXkgYWxsb3cgeW91IHRvIGRlZmluZSB5b3VyIG93biBuZXR3b3JrIHN0cnVjdHVyZSAob3IgZXZlbiBsZWFybiBpdCkgd2l0aCBjZXJ0YWluIGNvbnN0cmFpbnRzLiBZb3UgaGF2ZSB0byBkZWNpZGUgd2hldGhlciB0aGlzIGZsZXhpYmlsaXR5IGlzIHN1ZmZpY2llbnQgZm9yIHlvdXIgcHVycG9zZXMuIFRoZW4gd2l0aGluIGEgcGFydGljdWxhciBuZXR3b3JrIHN0cnVjdHVyZSwgeW91IGNhbiBsZWFybiBwYXJhbWV0ZXJzIGdpdmVuIGEgc3BlY2lmaWMgdHJhaW5pbmcgZGF0YXNldC48L3A+JiN4QTsmI3hBOzxwPllvdSByYXJlbHkgaGFyZC1jb2RlIGJlaGF2aW9yIGluIEFJL01MIHNvbHV0aW9ucy4gSXQncyBhbGwgYWJvdXQgbW9kZWxsaW5nIHRoZSB1bmRlcmx5aW5nIHNpdHVhdGlvbiBhbmQgYWNjb21tb2RhdGluZyBkaWZmZXJlbnQgc2l0dWF0aW9ucyBieSB0d2Vha2luZyBlbGVtZW50cyBvZiB0aGUgbW9kZWwuPC9wPiYjeEE7JiN4QTs8cD5JbiB5b3VyIGV4YW1wbGUsIHBlcmhhcHMgeW91IG1pZ2h0IGhhdmUgdGhlIHJvYm90IGxlYXJuIGhvdyB0byBkZXRlY3Qgb2JzdGFjbGVzIChieSBhbmFseXppbmcgZWxlbWVudHMgaW4gdGhlIGVudmlyb25tZW50KSwgb3IgeW91IG1pZ2h0IGhhdmUgaXQga2VlcCB0cmFjayBvZiB3aGVyZSB0aGUgb2JzdGFjbGVzIHdlcmUgYW5kIHdoaWNoIHdheSB0aGV5IHdlcmUgbW92aW5nLjwvcD4mI3hBOw== 51 2014-05-14T00:36:31.000+0000 null null 0 0 0 null 10 7 2 2014-05-14T00:53:43.000+0000 13 0 PHA+T25lIGJvb2sgdGhhdCdzIGZyZWVseSBhdmFpbGFibGUgaXMgIlRoZSBFbGVtZW50cyBvZiBTdGF0aXN0aWNhbCBMZWFybmluZyIgYnkgSGFzdGllLCBUaWJzaGlyYW5pLCBhbmQgRnJpZWRtYW4gKHB1Ymxpc2hlZCBieSBTcHJpbmdlcik6IDxhIGhyZWY9Imh0dHA6Ly9zdGF0d2ViLnN0YW5mb3JkLmVkdS9+dGlicy9FbGVtU3RhdExlYXJuLyI+c2VlIFRpYnNoaXJhbmkncyB3ZWJzaXRlPC9hPi48L3A+JiN4QTsmI3hBOzxwPkFub3RoZXIgZmFudGFzdGljIHNvdXJjZSwgYWx0aG91Z2ggaXQgaXNuJ3QgYSBib29rLCBpcyBBbmRyZXcgTmcncyBNYWNoaW5lIExlYXJuaW5nIGNvdXJzZSBvbiBDb3Vyc2VyYS4gVGhpcyBoYXMgYSBtdWNoIG1vcmUgYXBwbGllZC1mb2N1cyB0aGFuIHRoZSBhYm92ZSBib29rLCBhbmQgUHJvZi4gTmcgZG9lcyBhIGdyZWF0IGpvYiBvZiBleHBsYWluaW5nIHRoZSB0aGlua2luZyBiZWhpbmQgc2V2ZXJhbCBkaWZ

#### Subtask 4: answering to questions about Spark related concepts

Please write a short description for the terms below---one to two short paragraphs for each term. Don't copy-paste; instead, write your own understanding.

1. What do the terms 'Spark Application', 'SparkSession', 'Transformations', 'Action', and 'Lazy Evaluation' mean in the context of Spark?

Write your descriptions in the next cell.

Your descriptions:

Spark Application:
A spark application is an application to process large amounts of data, so we can get useful information about it. A spark application has several things it does which makes computations fast. For example, in-memory computation or parallel computations. It stores the data on RDD’s (resilient distributed dataset), which you can do different operations on, and send the result back to the spark application. It also has Dataframes which I used on this project, where you can view the data more clearly (in columna). Spark applications runs on clusters. The application takes in a users input, and then executes it. The Spark application basically divided in two parts: the driver- and executor-process. The information in stored in the driver, while the executor performs the calculation (then gives the information back to the driver)


SparkSession:
A spark session is a part of the spark driver, where every unique user has its own session. With a spark session you can access the functionality of spark, so when you want to start working with data on spark, you begin with creating a spark session, and from there you can create dataframes, RDD’s and so on. You can then begin processing and extracting information from your data. A spark session is basically a starting point to begin performing computations on your data.


Transformations:
Transformations are basically methods you can use on your RDD’s or DataFrames. Different transformations are map(), filter(), distinct() and so on. Transformations take an RDD or DataFrame as input and gives a manipulated RDD or DataFrame as output. With distinct() for example you get the same RDD/DataFrame back, but without all the duplicates.


Action: 
Actions are in some way like tranformations, since they are methods you can use on your RDD or DataFrame. Actions give you information about the RDD/DF you are using them on, so if you do RDD.count() for example, you receive the number of elements that are in RDD. Other actions are collect(), take() and so on. The biggest difference between actions and transformations is that actions does not return a RDD, but rather data like a float/integer or the elements contained in the RDD (with collect()). Actions also does not change the data in the RDD/DF, while transformations does.


Lazy Evaluation: 
Lazy evaluation is where you do not evaluate something, until the evaluation is actually strictly needed. This saves unnecessary evaluation (you only evaluate when you need it), which in turn saves computation time. So if an action is called for example, the action is not called immediately, but only called when we use it for something. This could for example be: if you want to calculate a number for a variable, the calculation is not done until you actually use that variable, like printing it out for instance.